In [4]:
import numpy as np
import pandas as pd
import torch
import pyarrow
import plotly.express as px
import datasets
from datasets import Dataset, DatasetDict
import transformers
import sklearn
from sklearn.model_selection import train_test_split
import accelerate
from sklearn.preprocessing import LabelEncoder

In [5]:
import huggingface_hub
from huggingface_hub import login
login()

In [6]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cuda


# Fine tune DistilBERT with supplemental training data

In [7]:
path = "/home/narenprax/Documents/GitHub/stats133finalproject/Python/pandas_sup_cleaned.parquet"
sup = pd.read_parquet(path)
sup.drop(columns=['title'], inplace=True)
sup.rename(columns={'decade':'label'}, inplace=True)

label_encoder = LabelEncoder()
sup['label'] = label_encoder.fit_transform(sup['label'])

sup


label                                               text
0         1  the cellar by josh Campbell & Matt stuecken da...
1         1  ten thing I hate about you write by Karen mccu...
2         1  107 # 2 40 ] _dalmatian MARCH 17 , 1995 ext . ...
3         2  please copy and return | — — — _— — — — _ twel...
4         1  twelve monkey a original screenplay by David p...
...     ...                                                ...
2853      1  chronicle by Jamie vanderbilt base on the book...
2854      3  zootopia written by Jared Bush &amp ; phil joh...
2855      3  Zulu Dawn 1 . script appear on black screen : ...
2856      1  existenz written by David cronenberg fourth dr...
2857      3  " xxx " by Rich wilk August 26 , 2001 third dr...

[2459 rows x 2 columns]

In [8]:
train_df, test_df = train_test_split(sup, test_size=0.3, random_state=133)

train_data = train_df.to_dict(orient='records')
test_data = test_df.to_dict(orient='records')

train_dataset = Dataset.from_dict({
    'label': [item['label'] for item in train_data],  # Extract 'label' values
    'text': [item['text'] for item in train_data]  # Extract 'text' values
})

test_dataset = Dataset.from_dict({
    'label': [item['label'] for item in test_data],  # Extract 'label' values
    'text': [item['text'] for item in test_data]  # Extract 'text' values
})

hf_dataset = DatasetDict({
    'train': train_dataset,
    'test': test_dataset
})

# Step 6: Check the output
print(hf_dataset['test'][0])  # Print the first test example to check

{'label': 1, 'text': 'it written by chase palmer &amp ; cary fukunaga base on the novel by Stephen King studio draft 3-18-2014 OPEN on : rain . lash a windowpane . a piano plays somewhere off screen . Beethoven \'s fur elise . int . will bedroom - day a little boy gaze out into the storm . nervous , eager , sweet . meet GEORGE denbrough ( 9 ) . GEORGE you sure it \'s not too bad out there ? will ( 13 ) , he older brother , sit up in bed propped against a pile of pillow , surround by tissue and sheet of newspaper . headline and toy tell we this be the late 80\' -- October , 1987 to be exact . he put finish touch on a paper boat will do not be such a wuss . I would come if I be not die . now get the paraffin . GEORGE in the cellar ? will you want it to float or not , georgie ? go on . Storm \'s not gonna last forever . GEORGE okay , willy . George jump up obediently and go . CUT to : title card : october 1987 2 . int . will be house - day George hurry downstairs . he catch a glimpse of t

In [9]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased")

In [10]:
def preprocess_function(examples):
    return tokenizer(examples["text"], truncation=True)

In [11]:
sup_tokens = hf_dataset.map(preprocess_function, batched=True)

Map:   0%|          | 0/1721 [00:00<?, ? examples/s]

Map:   0%|          | 0/738 [00:00<?, ? examples/s]

In [12]:
from transformers import DataCollatorWithPadding

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

In [13]:
from transformers import DataCollatorWithPadding

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

In [14]:
from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer

model = AutoModelForSequenceClassification.from_pretrained("distilbert-base-uncased", num_labels=4)

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [15]:
training_args = TrainingArguments(
    output_dir="./results",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=5,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=sup_tokens["train"],
    eval_dataset=sup_tokens["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
)

trainer.train()

/tmp/ipykernel_1480/137275998.py:10: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


TrainOutput(global_step=1080, training_loss=1.2852024855437103, metrics={'train_runtime': 543.2065, 'train_samples_per_second': 15.841, 'train_steps_per_second': 1.988, 'total_flos': 1139922621788160.0, 'train_loss': 1.2852024855437103, 'epoch': 5.0})

## Pushing the model to the hub so I don't have to keep making it

In [16]:
trainer.push_to_hub("stats133finalproject")

model.safetensors:   0%|          | 0.00/268M [00:00<?, ?B/s]

training_args.bin:   0%|          | 0.00/5.30k [00:00<?, ?B/s]

Upload 2 LFS files:   0%|          | 0/2 [00:00<?, ?it/s]

CommitInfo(commit_url='https://huggingface.co/D4rthSi/results/commit/b3c00b04b0fc98a0697d4eb2b4948bb42e55816c', commit_message='stats133finalproject', commit_description='', oid='b3c00b04b0fc98a0697d4eb2b4948bb42e55816c', pr_url=None, repo_url=RepoUrl('https://huggingface.co/D4rthSi/results', endpoint='https://huggingface.co', repo_type='model', repo_id='D4rthSi/results'), pr_revision=None, pr_num=None)